In [1]:
import bokeh.models as bkm
import resampy
from bokeh.plotting import figure, output_file, show
from bokeh.layouts import layout
from BokehAudioPlayer import AudioPlayerModel
import base64
from io import BytesIO
import numpy as np
from scipy.io import wavfile
from scipy import signal
import pandas as pd
from bokeh import palettes
import matplotlib.pyplot as plt


from bokeh.io import output_notebook
output_notebook()


/Users/russell/anaconda/lib/python3.5/site-packages/numba/errors.py:102: UserWarning: Insufficiently recent colorama version found. Numba requires colorama >= 0.3.9
  warnings.warn(msg)


Loading BokehJS ...

## Example sine wave

Example taken from: https://docs.bokeh.org/en/latest/docs/gallery/slider.html

In [2]:
from bokeh.layouts import column, row
from bokeh.models import CustomJS, Slider
from bokeh.plotting import ColumnDataSource

x = np.linspace(0, 10, 500)
y = np.sin(x)

source = ColumnDataSource(data=dict(x=x, y=y))

plot = figure(y_range=(-10, 10), 
#               plot_width=400, plot_height=400
              aspect_ratio=1.5, sizing_mode='scale_width',
              x_axis_label='x', y_axis_label='y',
             )

plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

amp_slider = Slider(start=0.1, end=10, value=1, step=.1, title="Amplitude", width=100)
freq_slider = Slider(start=0.1, end=10, value=1, step=.1, title="Frequency", width=100)
phase_slider = Slider(start=0, end=6.4, value=0, step=.1, title="Phase", width=100)
offset_slider = Slider(start=-5, end=5, value=0, step=.1, title="Offset", width=100)

callback = CustomJS(args=dict(source=source, amp=amp_slider, freq=freq_slider, phase=phase_slider, offset=offset_slider),
                    code="""
    const data = source.data;
    const A = amp.value;
    const k = freq.value;
    const phi = phase.value;
    const B = offset.value;
    const x = data['x']
    const y = data['y']
    for (var i = 0; i < x.length; i++) {
        y[i] = B + A*Math.sin(k*x[i]+phi);
    }
    source.change.emit();
""")

amp_slider.js_on_change('value', callback)
freq_slider.js_on_change('value', callback)
phase_slider.js_on_change('value', callback)
offset_slider.js_on_change('value', callback)

layout = row(
    plot,
    column(amp_slider, freq_slider, phase_slider, offset_slider),
)

output_file("slider.html", title="slider.py example")

show(layout)

In [3]:
# (2) Make a beat

filename = 'Beat'
outfile = './'
TargetDuration = 2  # [s] length of signal
fsig1 = [200, 200]  # [Hz] frequency of input signal
fsig2 = [210, 300]
A1 = 0.5
A2 = 0.3

pi  = np.pi 

tabs = []
for ii, fsig in enumerate(fsig1):
    fs = 5*np.max([fsig1[ii], fsig2[ii]])  # Sampling frequency must be at least 2x the maximum frequency
      
    # Build time axis for target durdation
    t = np.arange(0,TargetDuration,1/fs)
    
    # Make 2 signals of similar frequency and add them together
    x1 = 2*pi*fsig1[ii]*t
    x2 = 2*pi*fsig2[ii]*t
    y1 = A1*np.sin(x1)
    y2 = A2*np.sin(x2)
    ysum = y1 + y2
    
    # Combine the 3 into a single waveform and taper so no sharp edges
    window = signal.tukey(len(t),alpha=0.1)  # window taper
    TargetDuration_cat = TargetDuration*3
    y = np.concatenate([y1*window, y2*window, ysum*window], axis=None)

    # # Set up title names
    default_title=filename  # will become output file name
    title=default_title.replace('_', ' ').title()
    plot_filename=default_title + '_' + str(TargetDuration) + 's' + '.html'

    # make plot and sonify
    # grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
    #                                       fs_resamp=44100,default_title=default_title,title=title)
    grid = AudioPlayerModel.sonify_plotwfspec(data=y,data_dis=y,fs=fs,TargetDuration=TargetDuration_cat,
                                          fs_resamp=44100,default_title=title,title=title,
                                          aspect_ratio=3,  # aspect ratio of individual plots
                                          # palette='RdYlBu11'
                                          palette = palettes.all_palettes['Magma'][256],
                                          seek_bar_color='limegreen',
                                          seek_bar_alpha=0.8,
                                          # palette='Viridis256'
                                          is_xtrue = False,
                                          is_ytrue = False,
                                          )             
    # Build tabs for different waveforms
    tab = bkm.Panel(child=grid, title=str(fsig1[ii])+'Hz + '+str(fsig2[ii])+'Hz')
    tabs.append(tab)

# Combine tabs in final plot
plot = bkm.Tabs(tabs=tabs)

output_file(outfile+filename+'.html')
# show(grid)
show(plot)

## Compare sine wave with square wave

In [4]:
filename = 'squarewave'
fsig = 200  # Hz
TargetDuration = 2  # [s] length of signal

fs = 30*fsig  # Sampling frequency must be at least 2x the maximum frequency
# Build time axis for target durdation
t = np.arange(0,TargetDuration,1/fs)

# Make 2 signals of similar frequency and add them together
x = 2*pi*fsig*t
y = np.sin(x)
#     ysq = np.sin(xsq)
ysq = signal.square(2 * np.pi * fsig * t)

# Combine the 3 into a single waveform and taper so no sharp edges
window = signal.tukey(len(t),alpha=0.1)  # window taper
TargetDuration_cat = TargetDuration*2
y = np.concatenate([y*window, ysq*window], axis=None)

# # Set up title names
default_title=filename  # will become output file name
title='Square wave vs. Sine wave ('+str(fsig)+' Hz)'
plot_filename=default_title + '_' + str(TargetDuration) + 's' + '.html'

# make plot and sonify
# grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
#                                       fs_resamp=44100,default_title=default_title,title=title)
grid = AudioPlayerModel.sonify_plotwfspec(data=y,data_dis=y,fs=fs,TargetDuration=TargetDuration_cat,
                                      fs_resamp=44100,default_title=title,title=title,
                                      aspect_ratio=3,  # aspect ratio of individual plots
                                      # palette='RdYlBu11'
                                      palette = palettes.all_palettes['Magma'][256],
                                      seek_bar_color='limegreen',
                                      seek_bar_alpha=0.8,
                                      # palette='Viridis256'
                                      is_xtrue = False,
                                      is_ytrue = False,
                                      )             

output_file(outfile+filename+'.html')
# show(grid)
show(grid)

## Demonstrate envelopes

This waveform is very simple but starts to approximate the shape of a seismogram. (looks more like a moonquake actually!)

In [5]:
filename = 'envelope'
outfile = './'
Duration = 2
TargetDurations = [2,5,8]
fsig = 440

tabs = []
fs = 5*fsig
Ncycles = fs*Duration
for ii, TargetDuration in enumerate(TargetDurations):
    
    # Make sine curve with desired duration keeping same number of cycles
    SpeedFactor = Duration/TargetDuration
    t = np.arange(0,TargetDuration,1/fs)
    x = 2*pi*fsig*t * SpeedFactor
    y = np.sin(x)
    
    # 1) make a curve that will be the envelope, of the same length as the original signal
    N = len(y)
    envelope = np.zeros(N)
    peak = int(N/6)

    # from 0 to the peak index (peak):
    up = np.linspace(0,1,peak)
    envelope[:peak] = up

    # and fill in the rest: 
    down = np.linspace(1,0,(N-peak))
    envelope[peak:] = down

    # modulate the signal by multiplication
    yenv = y*envelope

    # make plot and sonify
    # grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
    #                                       fs_resamp=44100,default_title=default_title,title=title)
    grid = AudioPlayerModel.sonify_plotwfspec(data=yenv,data_dis=yenv,fs=fs,TargetDuration=TargetDuration,
                                          fs_resamp=44100,default_title=filename,title=filename,
                                          aspect_ratio=3,  # aspect ratio of individual plots
                                          # palette='RdYlBu11'
                                          palette = palettes.all_palettes['Magma'][256],
                                          seek_bar_color='limegreen',
                                          seek_bar_alpha=0.8,
                                          # palette='Viridis256'
                                          is_xtrue = False,
                                          is_ytrue = False,
                                          )             
    # Build tabs for different waveforms
    tab = bkm.Panel(child=grid, title=str(TargetDuration)+' seconds')
    tabs.append(tab)

# Combine tabs in final plot
plot = bkm.Tabs(tabs=tabs)

output_file(outfile+filename+'.html')
# show(grid)
show(plot)